In [9]:
def geojson_to_separate_xlsx(geojson_files, output_folder):
    # Verificar se a pasta de saída existe, se não, criar
    os.makedirs(output_folder, exist_ok=True)
    
    for file in geojson_files:
        # Ler o arquivo GeoJSON usando geopandas
        gdf = gpd.read_file(file)
        
        # Verificar e definir CRS se necessário
        if gdf.crs is None:
            gdf.set_crs(epsg=31983, inplace=True)  # Defina o CRS correto, se necessário
        gdf = gdf.to_crs(epsg=4326)  # Converter para WGS84 (latitude e longitude)
        
        all_features = []
        
        for _, row in gdf.iterrows():
            geometry = row.geometry
            attributes = row.drop('geometry').to_dict()
            
            if geometry.type == 'Point':
                coords = geometry.coords[0]
                all_features.append({
                    'Latitude': coords[1],
                    'Longitude': coords[0],
                    **attributes
                })
            
            elif geometry.type == 'LineString':
                # Extrair todas as coordenadas
                for coord in geometry.coords:
                    all_features.append({
                        'Latitude': coord[1],
                        'Longitude': coord[0],
                        **attributes
                    })
            
            elif geometry.type == 'Polygon':
                # Extrair vértices do anel exterior do polígono
                for coord in geometry.exterior.coords:
                    all_features.append({
                        'Latitude': coord[1],
                        'Longitude': coord[0],
                        **attributes
                    })
            
            elif geometry.type == 'MultiLineString':
                for line in geometry.geoms:
                    for coord in line.coords:
                        all_features.append({
                            'Latitude': coord[1],
                            'Longitude': coord[0],
                            **attributes
                        })
            
            elif geometry.type == 'MultiPolygon':
                for polygon in geometry.geoms:
                    for coord in polygon.exterior.coords:
                        all_features.append({
                            'Latitude': coord[1],
                            'Longitude': coord[0],
                            **attributes
                        })
            else:
                print(f"Geometria não suportada: {geometry.type}")
        
        # Converter a lista de features em um DataFrame
        df_features = pd.DataFrame(all_features)
        
        # Salvar como Excel
        base_name = os.path.splitext(os.path.basename(file))[0]
        output_excel = os.path.join(output_folder, f'{base_name}.xlsx')
        df_features.to_excel(output_excel, index=False)
        print(f"Salvou {output_excel} com sucesso.")


## Mudar o crs dos arquivos

In [15]:
# Função para processar GeoJSONs e salvá-los no formato desejado
def processar_geojsons(arquivos_geojson, pasta_saida='dados_processados', crs_destino=4326, formato='GeoJSON'):
    # Verificar se a pasta de saída existe, senão, criar
    if not os.path.exists(pasta_saida):
        os.makedirs(pasta_saida)
    
    geojson_list = []
    
    for arquivo in arquivos_geojson:
        # Carregar o GeoJSON
        gdf = gpd.read_file(arquivo)
        
        # Verificar se o CRS já está no formato de destino
        if gdf.crs.to_epsg() != crs_destino:
            # Transformar para coordenadas globais (EPSG:4326) somente se necessário
            gdf = gdf.to_crs(epsg=crs_destino)
        
        # Verificar e limpar geometrias inválidas ou nulas
        gdf = gdf[gdf.is_valid].dropna(subset=['geometry'])
        
        # Nome do arquivo de saída
        nome_saida = os.path.join(pasta_saida, os.path.basename(arquivo).replace('.geojson', f'.{formato.lower()}'))
        
        # Salvar o arquivo no formato desejado
        if formato.lower() == 'geojson':
            gdf.to_file(nome_saida, driver='GeoJSON')
        elif formato.lower() == 'shapefile':
            gdf.to_file(nome_saida, driver='ESRI Shapefile')
        
        # Adicionar ao geojson_list
        geojson_list.append((arquivo, gdf))
    
    return geojson_list

In [16]:
# Lista de arquivos GeoJSON
arquivos_geojson = [
    'SAD69-96_SHP_areainfluenciametro.geojson',
    'SAD69-96_SHP_corredoronibus_line.geojson',
    'SAD69-96_SHP_estacaometro_point.geojson',
    'SAD69-96_SHP_estacaometroprojeto_point.geojson',
    'SAD69-96_SHP_estacaotrem.geojson',
    'SAD69-96_SHP_estacaotremprojeto_point.geojson',
    'SAD69-96_SHP_ferroviamdc.geojson',
    'SAD69-96_SHP_linhametro_line.geojson',
    'SAD69-96_SHP_linhametroprojeto.geojson',
    'SAD69-96_SHP_linhatrem.geojson',
    'SAD69-96_SHP_linhatremprojeto_line.geojson',
    'SAD69-96_SHP_pontoonibus.geojson',
    'sad6996_terminal_onibus.geojson',
]

# Processar os GeoJSONs e salvá-los
geojson_list = processar_geojsons(arquivos_geojson, formato='GeoJSON')

CRS atual do arquivo SAD69-96_SHP_areainfluenciametro.geojson: EPSG:4326
CRS atual do arquivo SAD69-96_SHP_corredoronibus_line.geojson: EPSG:4326
CRS atual do arquivo SAD69-96_SHP_estacaometro_point.geojson: EPSG:4326
CRS atual do arquivo SAD69-96_SHP_estacaometroprojeto_point.geojson: EPSG:4326
CRS atual do arquivo SAD69-96_SHP_estacaotrem.geojson: EPSG:4326
CRS atual do arquivo SAD69-96_SHP_estacaotremprojeto_point.geojson: EPSG:4326
CRS atual do arquivo SAD69-96_SHP_ferroviamdc.geojson: EPSG:4326
CRS atual do arquivo SAD69-96_SHP_linhametro_line.geojson: EPSG:4326
CRS atual do arquivo SAD69-96_SHP_linhametroprojeto.geojson: EPSG:4326
CRS atual do arquivo SAD69-96_SHP_linhatrem.geojson: EPSG:4326
CRS atual do arquivo SAD69-96_SHP_linhatremprojeto_line.geojson: EPSG:4326
CRS atual do arquivo SAD69-96_SHP_pontoonibus.geojson: EPSG:4326
CRS atual do arquivo sad6996_terminal_onibus.geojson: EPSG:4326


In [10]:

# Exemplo de uso
geojson_files = [
    'SAD69-96_SHP_areainfluenciametro_EPSG4326.geojson',
    'SAD69-96_SHP_corredoronibus_line_EPSG4326.geojson',
    'SAD69-96_SHP_estacaometro_point_EPSG4326.geojson',
    'SAD69-96_SHP_estacaometroprojeto_point_EPSG4326.geojson',
    'SAD69-96_SHP_estacaotrem_EPSG4326.geojson',
    'SAD69-96_SHP_estacaotremprojeto_point_EPSG4326.geojson',
    'SAD69-96_SHP_ferroviamdc_EPSG4326.geojson',
    'SAD69-96_SHP_linhametro_line_EPSG4326.geojson',
    'SAD69-96_SHP_linhametroprojeto_EPSG4326.geojson',
    'SAD69-96_SHP_linhatrem_EPSG4326.geojson',
    'SAD69-96_SHP_linhatremprojeto_line_EPSG4326.geojson',
    'SAD69-96_SHP_pontoonibus_EPSG4326.geojson',
    'sad6996_terminal_onibus_EPSG4326.geojson',
    ]  # Lista de arquivos GeoJSON
output_folder = 'output_xlsx_files'  # Pasta onde os arquivos Excel serão salvos
geojson_to_separate_xlsx(geojson_files, output_folder)

C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:20: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if geometry.type == 'Point':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:28: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  elif geometry.type == 'LineString':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:37: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  elif geometry.type == 'Polygon':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:20: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if geometry.type == 'Point':
C:\Users\Denil\Ap

Salvou output_xlsx_files\SAD69-96_SHP_areainfluenciametro_EPSG4326.xlsx com sucesso.


C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:20: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if geometry.type == 'Point':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:28: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  elif geometry.type == 'LineString':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:20: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if geometry.type == 'Point':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:28: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  elif geometry.type == 'LineString':
C:\Users\Denil

Salvou output_xlsx_files\SAD69-96_SHP_corredoronibus_line_EPSG4326.xlsx com sucesso.
Salvou output_xlsx_files\SAD69-96_SHP_estacaometro_point_EPSG4326.xlsx com sucesso.
Salvou output_xlsx_files\SAD69-96_SHP_estacaometroprojeto_point_EPSG4326.xlsx com sucesso.


C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:20: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if geometry.type == 'Point':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:20: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if geometry.type == 'Point':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:20: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if geometry.type == 'Point':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:20: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if geometry.type == 'Point':
C:\Users\Denil\AppData\Local

...

C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:20: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if geometry.type == 'Point':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:28: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  elif geometry.type == 'LineString':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:20: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if geometry.type == 'Point':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:28: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  elif geometry.type == 'LineString':
C:\Users\Denil

Salvou output_xlsx_files\SAD69-96_SHP_linhatrem_EPSG4326.xlsx com sucesso.
Salvou output_xlsx_files\SAD69-96_SHP_linhatremprojeto_line_EPSG4326.xlsx com sucesso.


C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:20: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if geometry.type == 'Point':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:28: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  elif geometry.type == 'LineString':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:20: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if geometry.type == 'Point':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:28: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  elif geometry.type == 'LineString':
C:\Users\Denil

Salvou output_xlsx_files\SAD69-96_SHP_pontoonibus_EPSG4326.xlsx com sucesso.
Salvou output_xlsx_files\sad6996_terminal_onibus_EPSG4326.xlsx com sucesso.


C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:20: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if geometry.type == 'Point':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:20: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if geometry.type == 'Point':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:20: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if geometry.type == 'Point':
C:\Users\Denil\AppData\Local\Temp\ipykernel_9028\1636174784.py:20: ShapelyDeprecationWarning: The 'type' attribute is deprecated, and will be removed in the future. You can use the 'geom_type' attribute instead.
  if geometry.type == 'Point':
C:\Users\Denil\AppData\Local

In [1]:
import geopandas as gpd

geojson_files = [
    'SAD69-96_SHP_ferroviamdc_EPSG4326.geojson',
    'SAD69-96_SHP_linhametro_line_EPSG4326.geojson',
    'SAD69-96_SHP_linhametroprojeto_EPSG4326.geojson',
    'SAD69-96_SHP_linhatrem_EPSG4326.geojson',
    'SAD69-96_SHP_linhatremprojeto_line_EPSG4326.geojson',
    'SAD69-96_SHP_corredoronibus_line_EPSG4326.geojson',
]

# Dicionário para armazenar as colunas de cada arquivo
columns_per_file = {}

# Loop pelos arquivos para extrair as colunas
for file in geojson_files:
    try:
        # Lê o GeoJSON usando geopandas
        gdf = gpd.read_file(file)
        # Armazena as colunas no dicionário
        columns_per_file[file] = gdf.columns.tolist()
    except Exception as e:
        print(f"Erro ao processar o arquivo {file}: {e}")

# Exibe as colunas de cada arquivo
for file, columns in columns_per_file.items():
    print(f"\nArquivo: {file}")
    print(f"Colunas: {columns}")



Arquivo: SAD69-96_SHP_ferroviamdc_EPSG4326.geojson
Colunas: ['fm_id', 'geometry']

Arquivo: SAD69-96_SHP_linhametro_line_EPSG4326.geojson
Colunas: ['lmt_nome', 'lmt_linom', 'lmt_empres', 'lmt_linha', 'geometry']

Arquivo: SAD69-96_SHP_linhametroprojeto_EPSG4326.geojson
Colunas: ['lmtp_linha', 'lmtp_empre', 'lmtp_nome', 'lmtp_linom', 'geometry']

Arquivo: SAD69-96_SHP_linhatrem_EPSG4326.geojson
Colunas: ['ltr_numero', 'ltr_empres', 'ltr_nome', 'geometry']

Arquivo: SAD69-96_SHP_linhatremprojeto_line_EPSG4326.geojson
Colunas: ['ltp_nrnome', 'ltp_situac', 'ltp_nome', 'ltp_empres', 'ltp_linha', 'geometry']

Arquivo: SAD69-96_SHP_corredoronibus_line_EPSG4326.geojson
Colunas: ['co_km', 'co_obs', 'co_ano', 'co_nome', 'co_id', 'geometry']


In [2]:
import geopandas as gpd

geojson_files = [
    'SAD69-96_SHP_ferroviamdc_EPSG4326.geojson',
    'SAD69-96_SHP_linhametro_line_EPSG4326.geojson',
    'SAD69-96_SHP_linhametroprojeto_EPSG4326.geojson',
    'SAD69-96_SHP_linhatrem_EPSG4326.geojson',
    'SAD69-96_SHP_linhatremprojeto_line_EPSG4326.geojson',
    'SAD69-96_SHP_corredoronibus_line_EPSG4326.geojson',
]

# Dicionário para armazenar as características de cada arquivo
info_per_file = {}

# Loop pelos arquivos para extrair as informações
for file in geojson_files:
    try:
        # Lê o GeoJSON usando geopandas
        gdf = gpd.read_file(file)
        # Extrai informações principais
        info_per_file[file] = {
            'Colunas': gdf.columns.tolist(),
            'Número de registros': len(gdf),
            'Tipo de geometria': gdf.geom_type.unique().tolist(),
            'Sistema de referência espacial (CRS)': gdf.crs.to_string() if gdf.crs else "Não definido",
            'Primeiras linhas': gdf.head(3).to_dict(orient='records'),  # Prévia dos dados
        }
    except Exception as e:
        print(f"Erro ao processar o arquivo {file}: {e}")

# Exibe as características de cada arquivo
for file, info in info_per_file.items():
    print(f"\nArquivo: {file}")
    for key, value in info.items():
        print(f"{key}: {value}")



Arquivo: SAD69-96_SHP_ferroviamdc_EPSG4326.geojson
Colunas: ['fm_id', 'geometry']
Número de registros: 2400
Tipo de geometria: ['LineString']
Sistema de referência espacial (CRS): EPSG:4326
Primeiras linhas: [{'fm_id': 8011232, 'geometry': <LINESTRING (338198.89 7389572.058, 338209.57 7389559.078)>}, {'fm_id': 8011104, 'geometry': <LINESTRING (326507.792 7397997.28, 326526.945 7397990.081, 326546.865 73979...>}, {'fm_id': 8011128, 'geometry': <LINESTRING (326507.792 7397997.28, 326507.644 7397997.348, 326505.158 73979...>}]

Arquivo: SAD69-96_SHP_linhametro_line_EPSG4326.geojson
Colunas: ['lmt_nome', 'lmt_linom', 'lmt_empres', 'lmt_linha', 'geometry']
Número de registros: 6
Tipo de geometria: ['LineString']
Sistema de referência espacial (CRS): EPSG:4326
Primeiras linhas: [{'lmt_nome': 'AZUL', 'lmt_linom': 'LINHA 1 - AZUL', 'lmt_empres': 'METRO', 'lmt_linha': 1, 'geometry': <LINESTRING (336347.634 7402505.9, 336236.084 7402374.727, 336185.111 740232...>}, {'lmt_nome': 'VERDE', 'lmt_li